In [1]:
import pandas as pd

In [10]:
import pandas as pd
from sentence_transformers import SentenceTransformer
#import umap.umap_ as umap
import matplotlib.pyplot as plt
import matplotlib.cm as cm
import numpy as np
from sklearn.feature_extraction.text import TfidfVectorizer
import pandas as pd
import nltk
from nltk.corpus import stopwords
from bertopic import BERTopic
import plotly.express as px
from sklearn.cluster import KMeans
import pandas as pd
from sentence_transformers import SentenceTransformer
#import umap.umap_ as umap
import json

In [2]:
df = pd.read_csv("../Data/raw/df_oilnews.csv")

In [6]:
import pandas as pd
import numpy as np
import re
import umap
import json
from gensim.models import KeyedVectors
from huggingface_hub import hf_hub_download


model_file = hf_hub_download(
    "fse/word2vec-google-news-300", filename="word2vec-google-news-300.model"
)
vectors_file = hf_hub_download(
    "fse/word2vec-google-news-300", filename="word2vec-google-news-300.model.vectors.npy"
)

w2v_model = KeyedVectors.load(model_file, mmap='r')
w2v_model.vectors = np.load(vectors_file)
w2v_model.fill_norms()

df['text'] = df['title'].astype(str) + " " + df['excerpt'].astype(str)
def simple_tokenize(text):
    return re.sub(r'[^\w\s]', '', text.lower()).split()
df['tokens'] = df['text'].apply(simple_tokenize)

vector_size = w2v_model.vector_size
def get_doc_embedding(tokens):
    vecs = [w2v_model[w] for w in tokens if w in w2v_model]
    return np.mean(vecs, axis=0) if vecs else np.zeros(vector_size)
embeddings = np.vstack(df['tokens'].map(get_doc_embedding).values)

embedding_2d = umap.UMAP(n_components=2, random_state=42).fit_transform(embeddings)
embedding_3d = umap.UMAP(n_components=3, random_state=42).fit_transform(embeddings)

df['embedding_2d_1'] = embedding_2d[:, 0]
df['embedding_2d_2'] = embedding_2d[:, 1]
df['embedding_3d_1'] = embedding_3d[:, 0]
df['embedding_3d_2'] = embedding_3d[:, 1]
df['embedding_3d_3'] = embedding_3d[:, 2]
df['embedding_original'] = [json.dumps(vec.tolist()) for vec in embeddings]

df.to_csv("news_embeddings_Word2Vec_HF_En.csv", index=False)


/opt/homebrew/lib/python3.11/site-packages/sklearn/utils/deprecation.py:151: FutureWarning: 'force_all_finite' was renamed to 'ensure_all_finite' in 1.6 and will be removed in 1.8.
  warnings.warn(
/opt/homebrew/lib/python3.11/site-packages/umap/umap_.py:1952: UserWarning: n_jobs value 1 overridden to 1 by setting random_state. Use no seed for parallelism.
  warn(
/opt/homebrew/lib/python3.11/site-packages/sklearn/utils/deprecation.py:151: FutureWarning: 'force_all_finite' was renamed to 'ensure_all_finite' in 1.6 and will be removed in 1.8.
  warnings.warn(
/opt/homebrew/lib/python3.11/site-packages/umap/umap_.py:1952: UserWarning: n_jobs value 1 overridden to 1 by setting random_state. Use no seed for parallelism.
  warn(


In [7]:
df

title        Date  \
0      April Price Crash Dragged Saudi Arabia’s Oil R...  2025-06-25   
1      Giant Leviathan Gas Field Offshore Israel Resu...  2025-06-25   
2      China and India Cut Imports of Lower-Quality C...  2025-06-25   
3      Iran-Israel War Prompts China to Reconsider Ru...  2025-06-25   
4        EU Set to Change Subsidy Rules for Energy Costs  2025-06-25   
...                                                  ...         ...   
23415  Australia's Desalinization Plant Workers in In...  2011-06-20   
23416       Chinese Energy Workers in Somalia Threatened  2011-06-19   
23417  Argentina Now Receiving 40 Percent of Chinese ...  2011-06-19   
23418  Chinese Dam and Pipeline Projects Raise Burmes...  2011-06-18   
23419  Russia Remains Committed to Burgas-Alexandroup...  2011-06-18   

                                                 excerpt  \
0      Saudi Arabia’s revenues from oil exports crash...   
1      The massive Leviathan gas field offshore Israe...   
2      The world’s biggest and second-biggest coal im...   
3      The war between Israel and Iran has spark worr...   
4      National governments in the EU would soon be a...   
...                                                  ...   
23415  Victoria state’s troubled Wonthaggi desalinati...   
23416  The Ogaden National Liberation Front has warne...   
23417  In Argentina Mandarin Chinese is now the main ...   
23418  Lucrative China-backed hydropower projects are...   
23419  Russian Deputy Energy Minister Anatoli Ianovsk...   

                                                    text  \
0      April Price Crash Dragged Saudi Arabia’s Oil R...   
1      Giant Leviathan Gas Field Offshore Israel Resu...   
2      China and India Cut Imports of Lower-Quality C...   
3      Iran-Israel War Prompts China to Reconsider Ru...   
4      EU Set to Change Subsidy Rules for Energy Cost...   
...                                                  ...   
23415  Australia's Desalinization Plant Workers in In...   
23416  Chinese Energy Workers in Somalia Threatened T...   
23417  Argentina Now Receiving 40 Percent of Chinese ...   
23418  Chinese Dam and Pipeline Projects Raise Burmes...   
23419  Russia Remains Committed to Burgas-Alexandroup...   

                                                  tokens  embedding_2d_1  \
0      [april, price, crash, dragged, saudi, arabias,...        4.076112   
1      [giant, leviathan, gas, field, offshore, israe...        1.452281   
2      [china, and, india, cut, imports, of, lowerqua...        3.568454   
3      [iranisrael, war, prompts, china, to, reconsid...        0.904133   
4      [eu, set, to, change, subsidy, rules, for, ene...       -1.379843   
...                                                  ...             ...   
23415  [australias, desalinization, plant, workers, i...        4.627802   
23416  [chinese, energy, workers, in, somalia, threat...        1.782296   
23417  [argentina, now, receiving, 40, percent, of, c...       -2.491417   
23418  [chinese, dam, and, pipeline, projects, raise,...       -2.496847   
23419  [russia, remains, committed, to, burgasalexand...        1.747395   

       embedding_2d_2  embedding_3d_1  embedding_3d_2  embedding_3d_3  \
0            2.706722        2.140065        2.913249        6.669215   
1            0.808311       -0.167522        0.551124        6.088664   
2            2.412405        3.249104        1.383142        4.504251   
3            0.095316        1.513685        0.096913        4.689708   
4            0.967619        1.885924        1.039358        3.399420   
...               ...             ...             ...             ...   
23415       -1.454180       -0.253716       -0.406463        7.479317   
23416       -1.918538        0.823132       -0.949996        5.545636   
23417        3.015398        1.657859        2.654010        2.610949   
23418        0.002027        1.109200        0.199374        2.233668   
23419        0.335611       

## Cluster Analysis

In [9]:
df_embeddings = pd.read_csv("../Data/raw/news_embeddings_Word2Vec_HF_En.csv")

In [11]:
df_subset = df_embeddings

X = df_subset[['embedding_2d_1', 'embedding_2d_2']].values
k = 20  
kmeans = KMeans(n_clusters=k, random_state=42)
clusters = kmeans.fit_predict(X)
df_subset['cluster'] = clusters.astype(str)

big_palette = px.colors.qualitative.Safe + px.colors.qualitative.Bold + px.colors.qualitative.Light24
colors_for_clusters = big_palette[:k]

fig = px.scatter(
    df_subset,
    x='embedding_2d_1',
    y='embedding_2d_2',
    color='cluster',
    color_discrete_sequence=colors_for_clusters,
    hover_name='title',
    title=f'Cluster analysis con {k} cluster',
    width=900,
    height=700
)

fig.update_traces(marker=dict(size=8, opacity=0.7))
fig.show()


### Cluster Semantics

In [12]:
nltk.download('stopwords')
stop_words = stopwords.words('english')

def descrivi_cluster(df, n_top_words=20):
    descrizioni = {}
    for cluster_id in sorted(df['cluster'].unique()):
        testi = df[df['cluster'] == cluster_id]['title'].values
        testo_unito = " ".join(testi)
        vectorizer = TfidfVectorizer(stop_words=stop_words, max_features=1000)
        tfidf_matrix = vectorizer.fit_transform([testo_unito])
        feature_names = vectorizer.get_feature_names_out()
        scores = tfidf_matrix.toarray()[0]
        top_indices = scores.argsort()[-n_top_words:][::-1]
        top_words = [feature_names[i] for i in top_indices]
        descrizioni[cluster_id] = ", ".join(top_words)
    return descrizioni

descrizioni = descrivi_cluster(df_subset)
for cluster, parole in descrizioni.items():
    print(f"Cluster {cluster}: {parole}")


[nltk_data] Downloading package stopwords to
[nltk_data]     /Users/saraborello/nltk_data...
[nltk_data]   Package stopwords is already up-to-date!


Cluster 0: oil, gas, offshore, production, shale, drilling, new, field, natural, exploration, china, sea, discovery, billion, energy, exxon, first, north, opec, lng
Cluster 1: energy, billion, oil, uk, gas, tax, climate, investment, new, industry, could, power, windfall, china, fossil, crisis, clean, change, transition, world
Cluster 10: pipeline, oil, court, mountain, trans, keystone, gas, xl, case, stream, new, nord, judge, bp, billion, canada, could, energy, enbridge, dakota
Cluster 11: nuclear, power, plant, energy, plants, iran, japan, new, uk, russia, reactor, blackouts, grid, reactors, china, could, electricity, fukushima, build, first
Cluster 12: oil, crude, prices, build, api, draw, reports, inventory, inventories, surprise, gasoline, large, rise, fall, draws, small, higher, product, expected, rally
Cluster 13: oil, refinery, strike, pipeline, production, crude, libya, gulf, mexico, exports, largest, hurricane, workers, shut, shell, shuts, fuel, tanker, russian, sea
Cluster 14

In [13]:
descrizioni_cluster = {}

for cluster_id in sorted(df_subset['cluster'].unique()):
    testi_cluster = df_subset[df_subset['cluster'] == cluster_id]['title'].tolist()
    
    topic_model = BERTopic(language="english")
    topics, probs = topic_model.fit_transform(testi_cluster)
    parole_chiave = topic_model.get_topic(0)
    
    descrizioni_cluster[cluster_id] = parole_chiave


for cluster_id, parole in descrizioni_cluster.items():
    print(f"Cluster {cluster_id}:")
    print(", ".join([word for word, _ in parole]))
    print("-" * 50)


Cluster 0:
china, chinese, cnooc, chinas, south, gas, sinopec, major, giant, sea
--------------------------------------------------
Cluster 1:
uk, bills, energy, to, government, for, households, gas, in, wind
--------------------------------------------------
Cluster 10:
in, oil, court, for, to, of, us, over, case, the
--------------------------------------------------
Cluster 11:
blackouts, texas, grid, power, to, outages, electricity, avoid, coal, gas
--------------------------------------------------
Cluster 12:
oil, crude, prices, inventories, build, draw, inventory, on, surprise, us
--------------------------------------------------
Cluster 13:
libyas, libya, libyan, ports, majeure, force, oil, oilfield, field, production
--------------------------------------------------
Cluster 14:
eu, energy, to, prices, carbon, market, emission, deal, by, price
--------------------------------------------------
Cluster 15:
nigeria, libya, nigerias, angola, to, crude, exports, kenya, nigerian, 

| Cluster ID | Label                                    | Description                                                                                                                                  |
| :--------: | :--------------------------------------- | :------------------------------------------------------------------------------------------------------------------------------------------- |
|      0     | Offshore Oil & Gas Exploration           | Offshore oil and gas production, new field discoveries, shale, drilling, often linked to China and major companies (Exxon, OPEC, LNG).       |
|      1     | Energy Policy & Climate Transition       | Energy sector investments, climate policy, taxes, clean energy transition, global and UK/China focus.                                        |
|      2     | Oil Tanker Attacks & Geopolitical Risks  | Oil tanker and pipeline attacks, fires, explosions, and geopolitical instability involving Iran, Russia, Libya, and armed groups.            |
|      3     | Oil, Gas & LNG Trade Flows               | Trends in oil, gas, and LNG production, exports, imports, prices, and demand, with focus on China, OPEC, Russia, and global trade.           |
|      4     | Oil & Gas Projects and Deals             | Major oil/gas project announcements, field developments, deals, and investments, especially with Shell, Exxon, BP, and in Mexico/Iran/China. |
|      5     | Oil & Gas Earnings and Profits           | Company profits, earnings reports, estimates, losses, and financial performance of major oil and gas companies (Exxon, Shell, BP).           |
|      6     | Sanctions & Oil Trade Restrictions       | Oil and gas sanctions, export bans, price caps involving Iran, Russia, Venezuela, China, and OPEC.                                           |
|      7     | Oil & Gas Prices and Market Trends       | Oil and gas prices, demand fluctuations, weekly trends, gasoline prices, supply, and market forecasts.                                       |
|      8     | Electric Vehicles & Battery Industry     | Tesla, electric vehicles (EVs), batteries, Chinese car market, sales, technology, and new EV developments.                                   |
|      9     | Oil Majors, Deals & Assets               | Large oil companies (Aramco, Exxon, BP), asset sales, IPOs, deals, investments, and new business plans.                                      |
|     10     | Oil Pipelines & Legal Disputes           | Pipeline projects, legal cases (Keystone XL, Dakota, Enbridge), courts, and regulatory issues in the oil/gas sector.                         |
|     11     | Nuclear Energy & Power Grids             | Nuclear power plants, reactors, blackouts, electricity grid issues, nuclear incidents (Fukushima), Iran/Japan/Russia/UK/China nuclear news.  |
|     12     | Oil Inventories & Price Reports          | Oil and crude inventories, API reports, surprises in draws/builds, gasoline, product inventories, and price rallies.                         |
|     13     | Refineries, Strikes & Supply Disruptions | Refineries, strikes, hurricanes, pipeline issues, Gulf/Mexico production, shutdowns, export disruptions, and labor actions.                  |
|     14     | Energy Policy & Climate Regulations      | EU/UK/US energy policy, drilling/fracking bans, climate legislation, emissions, coal, and regulations (Trump/Biden focus).                   |
|     15     | OPEC, Russia, & Oil Production Cuts      | OPEC and Russia production decisions, Saudi/Indian/Chinese imports/exports, crude price deals, supply cuts, and market impacts.              |
|     16     | Oil Exports & Production Volumes         | Oil production/export statistics (bpd, millions), records, Russian/Indian/Chinese trade, high/record output, barrels/year, OPEC.             |
|     17     | Russia, Gas & Geopolitics                | Russia, gas pipelines, sanctions, EU/Ukraine, LNG, Nord Stream, Gazprom, nuclear, Iran, Saudi, and European energy security.                 |
|     18     | Renewable Energy & Capacity Growth       | Solar, wind, renewables, coal phase-out, global energy transition, emissions, carbon, capacity expansions (China, India, UK).                |
|     19     | Oil, Gas Demand & Price Dynamics         | Oil and gas demand, prices, global growth, industry cycles, low prices, shale, OPEC, and market forecasts.                                   |


In [15]:
df_subset['year'] = pd.to_datetime(df_subset['Date']).dt.year.astype(str)
X = df_subset[['embedding_2d_1', 'embedding_2d_2']].values

k = 20
kmeans = KMeans(n_clusters=k, random_state=42)
clusters = kmeans.fit_predict(X)

df_subset['cluster'] = clusters.astype(str)
big_palette = px.colors.qualitative.Safe + px.colors.qualitative.Bold + px.colors.qualitative.Light24
colors_for_clusters = big_palette[:k]

fig = px.scatter(
    df_subset,
    x='embedding_2d_1',
    y='embedding_2d_2',
    color='cluster',
    animation_frame='year',
    color_discrete_sequence=colors_for_clusters,
    hover_name='title',
    title=f'Cluster analysis con {k} cluster animata per anno',
    width=900,
    height=700
)

fig.update_traces(marker=dict(size=8, opacity=0.7))
fig.show()


## Feature Creation

In [16]:
import pandas as pd

df_embeddings['Date'] = pd.to_datetime(df_embeddings['Date'])

df_daily_mean = df_embeddings.groupby(df_embeddings['Date'].dt.date).agg({
    'embedding_2d_1': 'mean',
    'embedding_2d_2': 'mean',
    'embedding_3d_1': 'mean',
    'embedding_3d_2': 'mean',
    'embedding_3d_3': 'mean'
}).reset_index()

# Rinominare la colonna data in 'Date' (opzionale)
df_daily_mean.rename(columns={'Date': 'date'}, inplace=True)
df_daily_mean.rename(columns={
    col: f"{col}_mean" for col in df_daily_mean.columns if col not in ['date']
}, inplace=True)

df_daily_mean.head()


date  embedding_2d_1_mean  embedding_2d_2_mean  embedding_3d_1_mean  \
0  2011-06-18            -0.374726             0.168819             1.308357   
1  2011-06-19            -0.354561             0.548430             1.240495   
2  2011-06-20             1.349736            -0.693626             1.392533   
3  2011-06-21            -1.341812             0.129342             1.286522   
4  2011-06-22             0.400725             0.079165             0.873506   

   embedding_3d_2_mean  embedding_3d_3_mean  
0             0.344546             3.693299  
1             0.852007             4.078292  
2            -0.107635             5.247386  
3             0.327610             3.710636  
4             0.346109             4.371677

In [17]:
# Raggruppa per giorno e calcola la varianza sulle colonne degli embeddings
df_embeddings['Date'] = pd.to_datetime(df_embeddings['Date'])
df_daily_var = df_embeddings.groupby(df_embeddings['Date'].dt.date).agg({
    'embedding_2d_1': 'var',
    'embedding_2d_2': 'var',
    'embedding_3d_1': 'var',
    'embedding_3d_2': 'var',
    'embedding_3d_3': 'var'
}).reset_index()

df_daily_var.rename(columns={'Date': 'date'}, inplace=True)
df_daily_var.rename(columns={
    col: f"{col}_var_daily" for col in df_daily_var.columns if col not in ['date']
}, inplace=True)
df_daily_var['semantic_dispersion_2d'] = df_daily_var[['embedding_2d_1_var_daily', 'embedding_2d_2_var_daily']].mean(axis=1, skipna=True)
df_daily_var['semantic_dispersion_3d'] = df_daily_var[['embedding_3d_1_var_daily', 'embedding_3d_2_var_daily', 'embedding_3d_3_var_daily']].mean(axis=1, skipna=True)
df_daily_var.head()


date  embedding_2d_1_var_daily  embedding_2d_2_var_daily  \
0  2011-06-18                  9.006795                  0.055639   
1  2011-06-19                  9.132315                 12.171860   
2  2011-06-20                  8.230696                  1.220364   
3  2011-06-21                  5.131634                  0.972484   
4  2011-06-22                  3.308153                  2.559762   

   embedding_3d_1_var_daily  embedding_3d_2_var_daily  \
0                  0.079326                  0.042150   
1                  0.348385                  6.494428   
2                  1.355301                  0.877787   
3                  1.489803                  0.814485   
4                  0.528086                  1.355651   

   embedding_3d_3_var_daily  semantic_dispersion_2d  semantic_dispersion_3d  
0                  4.261042                4.531217                1.460840  
1                  4.306194               10.652088                3.716335  
2                  3.047017                4.725530                1.760035  
3                  2.598364                3.052059                1.634217  
4                  1.930240                2.933957                1.271326

In [18]:
import pandas as pd
import numpy as np
import ast
from sklearn.metrics.pairwise import cosine_similarity

df_embeddings['embedding_array'] = df_embeddings['embedding_original'].apply(ast.literal_eval).apply(np.array)

df_daily = df_embeddings.groupby(df_embeddings['Date'].dt.date)['embedding_array'].apply(lambda x: np.mean(np.stack(x), axis=0)).reset_index()
df_daily.rename(columns={'Date': 'date', 'embedding_array': 'embedding_mean'}, inplace=True)

def cosine_sim(v1, v2):
    return cosine_similarity(v1.reshape(1, -1), v2.reshape(1, -1))[0][0]

df_daily['cosine_sim'] = np.nan
for i in range(1, len(df_daily)):
    df_daily.loc[i, 'cosine_sim'] = cosine_sim(df_daily.loc[i, 'embedding_mean'], df_daily.loc[i-1, 'embedding_mean'])


df_daily['drift'] = 1 - df_daily['cosine_sim']

window_size = 3 
df_daily['drift_velocity'] = df_daily['drift'].rolling(window=window_size).mean()

df_daily['drift_velocity_diff'] = df_daily['drift_velocity'].diff()
df_daily['drift_acceleration'] = df_daily['drift_velocity_diff'].diff()

print(df_daily[['date', 'cosine_sim', 'drift', 'drift_velocity', 'drift_acceleration']].head(10))


         date  cosine_sim     drift  drift_velocity  drift_acceleration
0  2011-06-18         NaN       NaN             NaN                 NaN
1  2011-06-19    0.800558  0.199442             NaN                 NaN
2  2011-06-20    0.833325  0.166675             NaN                 NaN
3  2011-06-21    0.871855  0.128145        0.164754                 NaN
4  2011-06-22    0.918565  0.081435        0.125419                 NaN
5  2011-06-23    0.904230  0.095770        0.101783            0.015700
6  2011-06-24    0.735997  0.264003        0.147070            0.068921
7  2011-06-25    0.706760  0.293240        0.217671            0.025315
8  2011-06-26    0.785924  0.214076        0.257106           -0.031166
9  2011-06-27    0.885927  0.114073        0.207129           -0.089412


In [19]:
df_daily.dropna(inplace=True)

In [20]:
df_daily['date'] = pd.to_datetime(df_daily['date'])
df_daily_var['date'] = pd.to_datetime(df_daily_var['date'])
df_daily_var = df_daily_var.dropna()
df_daily_mean['date'] = pd.to_datetime(df_daily_mean['date'])

df_merged = pd.merge(df_daily, df_daily_var, on='date', how='inner')
df_merged = pd.merge(df_merged, df_daily_mean, on='date', how='inner')

In [21]:
df_merged.to_csv('embeddings_feature_news_embeddings_Word2Vec_HF_En.csv',index=False)